# Equation Discovery with Symbolic Regression to Paramterize Heat Flux in the Atmospheric Boundary Layer

*Authors: Antony Sikorski*

This notebook should make it easy to perform equation discovery with the use of the function `discover_eqs`. 

This function uses a number of supporting functions from the accompanying `functions.py` file, and should output a dataframe of possible equations.

We use the `PySR` package for symbolic regression, an ML method for finding interpretable symbolic expressions.

In [1]:
#importing libraries
# from pdfs import *
import os
import re

import xarray as xr
import netCDF4 as nc
import h5netcdf

import numpy as np
import matplotlib.pyplot as plt
from IPython.display import display
import pandas as pd

import pysr
from pysr import PySRRegressor

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score

from functions import *

Detected IPython. Loading juliacall extension. See https://juliapy.github.io/PythonCall.jl/stable/compat/#IPython


Some quick data processing: 

In [2]:
path = 'C:/Users/anton/Desktop/Career/LEAP_nyc_Summer2024/les_sim_2/'

directories, items = list_directories_files(path)
print("Directories starting with 'Ug':", directories)
print("Files starting with 'Ug':", items)

Directories starting with 'Ug': []
Files starting with 'Ug': ['Ug16Q000_IV.nc', 'Ug16Q001_IV.nc', 'Ug16Q003_IV.nc', 'Ug16Q006_I.nc', 'Ug16Q006_IV.nc', 'Ug16Q010_IV.nc', 'Ug1Q01_II.nc', 'Ug2Q010_I.nc', 'Ug2Q010_IV.nc', 'Ug2Q01_III.nc', 'Ug2Q024_I.nc', 'Ug8Q003_II.nc', 'Ug8Q003_III.nc', 'Ug8Q003_IV.nc', 'Ug8Q006_IV.nc']


In [3]:
for item in items:
    ds_stat = nc.Dataset( os.path.join(path, item), mode='r')
    if 'budget' in ds_stat.groups:
        print ("budget is in", item)
    else:
        print ("budget is not in", item)

budget is not in Ug16Q000_IV.nc
budget is in Ug16Q001_IV.nc
budget is in Ug16Q003_IV.nc
budget is in Ug16Q006_I.nc
budget is in Ug16Q006_IV.nc
budget is in Ug16Q010_IV.nc
budget is in Ug1Q01_II.nc
budget is in Ug2Q010_I.nc
budget is in Ug2Q010_IV.nc
budget is in Ug2Q01_III.nc
budget is in Ug2Q024_I.nc
budget is in Ug8Q003_II.nc
budget is in Ug8Q003_III.nc
budget is in Ug8Q003_IV.nc
budget is in Ug8Q006_IV.nc


In [4]:
for item in items[1:]:
    print(item)
    df = nc.Dataset(path + '/' + item, mode='r')
    print(df)

Ug16Q001_IV.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF4 data model, file format HDF5):
    dimensions(sizes): z(384), zh(385), time(120)
    variables(dimensions): float64 time(time), float64 z(z), float64 zh(zh)
    groups: default, thermo, budget
Ug16Q003_IV.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF4 data model, file format HDF5):
    dimensions(sizes): z(384), zh(385), time(120)
    variables(dimensions): float64 time(time), float64 z(z), float64 zh(zh)
    groups: default, thermo, budget
Ug16Q006_I.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF4 data model, file format HDF5):
    dimensions(sizes): z(256), zh(257), time(120)
    variables(dimensions): float64 time(time), float64 z(z), float64 zh(zh)
    groups: default, thermo, budget
Ug16Q006_IV.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF4 data model, file format HDF5):
    dimensions(sizes): z(384), zh(385), time(90)
    variables(dimensions): float64 time(time), float64 z(z), f

In [5]:
target_z_dim = 384

selected_files = []

for item in items[1:]:
        df = nc.Dataset(os.path.join(path, item), mode='r')
        if df.dimensions['z'].size == target_z_dim:
            selected_files.append(item)
        df.close()


print("Total number of files: ", len(items))
print("Number of valid files (same z and zh dims): ", len(selected_files))
print("Valid files: ", selected_files)

Total number of files:  15
Number of valid files (same z and zh dims):  11
Valid files:  ['Ug16Q001_IV.nc', 'Ug16Q003_IV.nc', 'Ug16Q006_IV.nc', 'Ug16Q010_IV.nc', 'Ug1Q01_II.nc', 'Ug2Q010_IV.nc', 'Ug2Q01_III.nc', 'Ug8Q003_II.nc', 'Ug8Q003_III.nc', 'Ug8Q003_IV.nc', 'Ug8Q006_IV.nc']


In [6]:
#eqs_Ug16Q001_IV = discover_eqs(path, ['Ug16Q001_IV.nc'], time_avg = 15, indices = np.s_[:, 0:200], difficulty = "hard")

In [7]:
# eqs_Ug16Q001_IV

In [8]:
#eqs_Ug2Q010_IV = discover_eqs(path, ['Ug2Q010_IV.nc'], time_avg = 15, indices = np.s_[:, 0:200], difficulty = "hard")

In [9]:
# eqs_Ug2Q010_IV

In [10]:
eqs_easy_mm = discover_eqs(path, selected_files, time_avg = 15, indices = np.s_[:, 0:200], difficulty = "easy", normChoice = "zscore")
eqs_medium_mm = discover_eqs(path, selected_files, time_avg = 15, indices = np.s_[:, 0:200], difficulty = "medium", normChoice = "zscore")
eqs_mediumhard_mm = discover_eqs(path, selected_files, time_avg = 15, indices = np.s_[:, 0:200], difficulty = "mediumhard", normChoice = "zscore")
eqs_hard_mm = discover_eqs(path, selected_files, time_avg = 15, indices = np.s_[:, 0:200], difficulty = "hard", normChoice = "zscore")

Don't forget to unnormalize the coef (zscore)
Compiling Julia backend...


[ Info: Started!



Expressions evaluated per second: 1.980e+03
Head worker occupation: 33.8%
Progress: 66 / 120000 total iterations (0.055%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
3           1.957e-01  5.314e+00  y = -0.96213 * sigma_th
5           4.837e-02  6.987e-01  y = (Mult * 0.3837) - sigma_th
7           2.969e-02  2.441e-01  y = ((wtheta - Mult) * -0.19459) - sigma_th
9           2.553e-02  7.549e-02  y = ((0.46457 * 0.51235) * (Mult - wtheta)) - sigma_th
11          1.928e-02  1.403e-01  y = ((0.38997 * Mult) - sigma_th) - ((sigma_th + wtheta) * 0.1...
                                  3594)
---------------------------------------------------------------------------------------------------
Press 'q' and then <enter> to stop execution early.

Expressions evaluated per second: 2.600e+03
Head worker occupation: 16.2%
Progress: 219 / 120000 total iterations (0.182%)
Hall of Fame:
-

[ Info: Started!



Expressions evaluated per second: 3.520e+03
Head worker occupation: 26.2%
Progress: 144 / 120000 total iterations (0.120%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+00  1.594e+01  y = 0.0039976
3           1.917e-01  8.260e-01  y = sigma_th / -1.113
5           6.272e-02  5.586e-01  y = (-0.36685 * wtheta) - sigma_th
7           5.553e-02  6.087e-02  y = ((dTheta_dz - wtheta) * 0.20464) - sigma_th
9           5.165e-02  3.622e-02  y = (dTheta_dz * 0.15358) - (sigma_th + (wtheta * 0.35525))
11          3.690e-02  1.682e-01  y = ((-0.15249 * sigma_th) * wtheta) + ((wtheta * -0.27608) - ...
                                  sigma_th)
15          3.681e-02  5.556e-04  y = ((0.052387 * 1.077) - (sigma_th + 0.048023)) - ((wtheta * ...
                                  0.14644) * (1.9427 + sigma_th))
17          3.567e-02  1.577e-02  y = ((-0.95704 * sigma_th) 

[ Info: Started!



Expressions evaluated per second: 3.200e+03
Head worker occupation: 22.8%
Progress: 128 / 120000 total iterations (0.107%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.251e+00  1.594e+01  y = -0.50145
3           1.917e-01  9.381e-01  y = -0.90235 * sigma_th
5           4.832e-02  6.890e-01  y = (Mult * 0.3959) - sigma_th
7           2.793e-02  2.740e-01  y = ((wtheta - Mult) * -0.20286) - sigma_th
9           2.536e-02  4.841e-02  y = ((0.49364 + -0.26382) * (Mult - wtheta)) - sigma_th
11          2.381e-02  3.150e-02  y = ((0.49364 + -0.26382) * (Mult - wtheta)) - (sigma_th * 1.0...
                                  362)
---------------------------------------------------------------------------------------------------
Press 'q' and then <enter> to stop execution early.

Expressions evaluated per second: 3.160e+03
Head worker occupation: 17.2%
Progress: 264 / 

[ Info: Started!



Expressions evaluated per second: 2.680e+03
Head worker occupation: 9.8%
Progress: 112 / 120000 total iterations (0.093%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
3           1.918e-01  5.314e+00  y = sigma_th * -0.88922
5           6.269e-02  5.590e-01  y = (-0.36994 * wtheta) - sigma_th
7           5.679e-02  4.940e-02  y = (sigma_th * -0.94415) - (0.39101 * wtheta)
9           5.620e-02  5.213e-03  y = ((-0.0060201 - 0.19292) * (wtheta - dTheta_dz)) - sigma_th
11          5.302e-02  2.917e-02  y = (wtheta + (sigma_th + sigma_th)) * (-0.42358 + (-0.02138 *...
                                   sigma_th))
13          5.127e-02  1.680e-02  y = ((wtheta - 0.068316) + (sigma_th + sigma_th)) * (-0.42358 ...
                                  + (-0.02138 * sigma_th))
17          4.903e-02  1.116e-02  y = ((-0.75834 - sigma_th) + (-0.32842 * wtheta)) + ((0.56964 ...
           

In [11]:
display(eqs_easy_mm)
display(eqs_medium_mm)
display(eqs_mediumhard_mm)
display(eqs_hard_mm)

complexity      loss     score  \
0           1  0.999939  0.000000   
1           3  0.191674  0.825949   
2           5  0.048306  0.689115   
3           7  0.025354  0.322318   
4           9  0.023555  0.036797   
5          11  0.018804  0.112628   
6          13  0.017279  0.042302   
7          15  0.017266  0.000373   
8          17  0.016671  0.017524   
9          19  0.014693  0.063143   

                                            equation  \
0                                        5.447857e-5   
1                              -0.8991735 * sigma_th   
2                     (0.39187944 * Mult) - sigma_th   
3          ((Mult - wtheta) * 0.23077033) - sigma_th   
4  (0.23845075 * (Mult - wtheta)) - (sigma_th * 1...   
5  ((Mult / 2.7501633) - (sigma_th / 0.90127444))...   
6  ((sigma_th + wtheta) / (-8.925714 + Mult)) + (...   
7  ((Mult / 2.359352) - (sigma_th + -0.0035517225...   
8  ((0.8666301 ^ wtheta) - (1.1184545 ^ sigma_th)...   
9  ((0.3582861 * Mult) - (sigma_th * 1.3175238)) ...   

                                        sympy_format  \
0                                5.44785700000000e-5   
1                                -0.8991735*sigma_th   
2                         0.39187944*Mult - sigma_th   
3     0.23077033*Mult - sigma_th - 0.23077033*wtheta   
4  0.23845075*Mult - 1.0418817*sigma_th - 0.23845...   
5  0.363614771530112*Mult - 1.10953995322446*sigm...   
6  0.423845191391535*Mult - sigma_th + (sigma_th ...   
7  0.423845191391535*Mult - sigma_th + 0.00355172...   
8  0.8666301**wtheta - 1.1184545**sigma_th + 0.38...   
9  -0.74502885**sigma_th + 0.8435401**wtheta + 0....   

                                       lambda_format  
0             PySRFunction(X=>0.0000544785700000000)  
1               PySRFunction(X=>-0.8991735*sigma_th)  
2        PySRFunction(X=>0.39187944*Mult - sigma_th)  
3  PySRFunction(X=>0.23077033*Mult - sigma_th - 0...  
4  PySRFunction(X=>0.23845075*Mult - 1.0418817*si...  
5  PySRFunction(X=>0.363614771530112*Mult - 1.109...  
6  PySRFunction(X=>0.423845191391535*Mult - sigma...  
7  PySRFunction(X=>0.423845191391535*Mult - sigma...  
8  PySRFunction(X=>0.8666301**wtheta - 1.1184545*...  
9  PySRFunction(X=>-0.74502885**sigma_th + 0.8435...

complexity      loss     score  \
0           1  0.999939  0.000000   
1           3  0.191674  0.825949   
2           5  0.062681  0.558866   
3           7  0.050671  0.106354   
4           9  0.036474  0.164381   
5          11  0.031759  0.069213   
6          13  0.027441  0.073059   
7          15  0.020463  0.146713   

                                            equation  \
0                                     -0.00015511311   
1                             -0.89910513 * sigma_th   
2                  (-0.37310132 * wtheta) - sigma_th   
3       (wtheta / (-2.8574662 - sigma_2)) - sigma_th   
4  ((wtheta * -0.14187771) * (sigma_th + 2.108475...   
5  (-1.1348178 * sigma_th) + ((1.4397421 + sigma_...   
6  ((wtheta * -0.17145114) - sigma_th) - ((-0.264...   
7  ((wtheta * -0.14187771) + (-1.0958452 * sigma_...   

                                        sympy_format  \
0                              -0.000155113110000000   
1                               -0.89910513*sigma_th   
2                      -sigma_th - 0.37310132*wtheta   
3          -sigma_th + wtheta/(-sigma_2 - 2.8574662)   
4  -sigma_th - 0.14187771*wtheta*(sigma_th + 2.10...   
5  -1.1348178*sigma_th + (dTheta_dz + 0.21364912)...   
6  -sigma_th - 0.17145114*wtheta - (-dTheta_dz - ...   
7  -1.0958452*sigma_th - 0.14187771*wtheta + (dTh...   

                                       lambda_format  
0             PySRFunction(X=>-0.000155113110000000)  
1              PySRFunction(X=>-0.89910513*sigma_th)  
2     PySRFunction(X=>-sigma_th - 0.37310132*wtheta)  
3  PySRFunction(X=>-sigma_th + wtheta/(-sigma_2 -...  
4  PySRFunction(X=>-sigma_th - 0.14187771*wtheta*...  
5  PySRFunction(X=>-1.1348178*sigma_th + (dTheta_...  
6  PySRFunction(X=>-sigma_th - 0.17145114*wtheta ...  
7  PySRFunction(X=>-1.0958452*sigma_th - 0.141877...

complexity      loss     score  \
0           1  0.999939  0.000000   
1           3  0.191674  0.825949   
2           5  0.048306  0.689115   
3           7  0.025354  0.322318   
4           9  0.023549  0.036929   
5          11  0.018807  0.112426   
6          13  0.017458  0.037201   
7          15  0.017441  0.000484   
8          17  0.016700  0.021717   
9          19  0.014694  0.063999   

                                            equation  \
0                                     -0.00010944141   
1                              sigma_th * -0.8991377   
2                      (Mult / 2.5520635) - sigma_th   
3          (0.23071174 * (Mult - wtheta)) - sigma_th   
4  (-0.24006625 * (wtheta - Mult)) - (sigma_th / ...   
5  (-0.13956133 * wtheta) - ((-0.36252597 * Mult)...   
6  ((Mult / 2.403044) - sigma_th) - ((sigma_th + ...   
7  ((Mult / 2.403044) - (sigma_th * 1.00471)) - (...   
8  ((0.865264 ^ wtheta) - (1.1226428 ^ sigma_th))...   
9  ((0.84530956 ^ wtheta) - (0.74671185 ^ sigma_t...   

                                        sympy_format  \
0                              -0.000109441410000000   
1                                -0.8991377*sigma_th   
2                  0.391839779848738*Mult - sigma_th   
3     0.23071174*Mult - sigma_th - 0.23071174*wtheta   
4  0.24006625*Mult - 1.04635006415695*sigma_th - ...   
5  0.36252597*Mult - 1.10821436190402*sigma_th - ...   
6  0.416138863874319*Mult - sigma_th - (sigma_th ...   
7  0.416138863874319*Mult - 1.00471*sigma_th - (s...   
8  0.865264**wtheta - 1.1226428**sigma_th + 0.388...   
9  -0.74671185**sigma_th + 0.84530956**wtheta + 0...   

                                       lambda_format  
0             PySRFunction(X=>-0.000109441410000000)  
1               PySRFunction(X=>-0.8991377*sigma_th)  
2  PySRFunction(X=>0.391839779848738*Mult - sigma...  
3  PySRFunction(X=>0.23071174*Mult - sigma_th - 0...  
4  PySRFunction(X=>0.24006625*Mult - 1.0463500641...  
5  PySRFunction(X=>0.36252597*Mult - 1.1082143619...  
6  PySRFunction(X=>0.416138863874319*Mult - sigma...  
7  PySRFunction(X=>0.416138863874319*Mult - 1.004...  
8  PySRFunction(X=>0.865264**wtheta - 1.1226428**...  
9  PySRFunction(X=>-0.74671185**sigma_th + 0.8453...

complexity      loss     score  \
0           1  0.999939  0.000000   
1           3  0.191674  0.825949   
2           5  0.062681  0.558866   
3           7  0.050679  0.106276   
4           9  0.036474  0.164453   
5          11  0.031831  0.068085   
6          13  0.027457  0.073908   
7          15  0.020494  0.146235   

                                            equation  \
0                                      -9.1864815e-5   
1                              -0.8990314 * sigma_th   
2                  (-0.37301287 * wtheta) - sigma_th   
3        (wtheta / (-2.842453 - sigma_2)) - sigma_th   
4  ((sigma_th + 2.1068926) * (wtheta * -0.1421538...   
5  (sigma_th / -0.8801135) - ((-0.21340553 - dThe...   
6  ((-0.17351812 * wtheta) - sigma_th) - ((-0.265...   
7  ((-0.13448471 * wtheta) - (sigma_th / 0.909681...   

                                        sympy_format  \
0                               -9.18648150000000e-5   
1                                -0.8990314*sigma_th   
2                      -sigma_th - 0.37301287*wtheta   
3           -sigma_th + wtheta/(-sigma_2 - 2.842453)   
4  -sigma_th - 0.14215383*wtheta*(sigma_th + 2.10...   
5  -1.13621709018212*sigma_th - (-dTheta_dz - 0.2...   
6  -sigma_th - 0.17351812*wtheta - (-dTheta_dz - ...   
7  -1.09928536557669*sigma_th - 0.13448471*wtheta...   

                                       lambda_format  
0            PySRFunction(X=>-0.0000918648150000000)  
1               PySRFunction(X=>-0.8990314*sigma_th)  
2     PySRFunction(X=>-sigma_th - 0.37301287*wtheta)  
3  PySRFunction(X=>-sigma_th + wtheta/(-sigma_2 -...  
4  PySRFunction(X=>-sigma_th - 0.14215383*wtheta*...  
5  PySRFunction(X=>-1.13621709018212*sigma_th - (...  
6  PySRFunction(X=>-sigma_th - 0.17351812*wtheta ...  
7  PySRFunction(X=>-1.09928536557669*sigma_th - 0...

In [40]:
eqs_easy_mm.iloc[5,4]

0.363614771530112*Mult - 1.10953995322446*sigma_th - 0.13961816*wtheta

In [33]:
eqs_medium_mm.iloc[7,4]

-1.0958452*sigma_th - 0.14187771*wtheta + (dTheta_dz + 0.24824809)*(sigma_2 + 1.3563443)

In [49]:
eqs_mediumhard_mm.iloc[5,4]

0.36252597*Mult - 1.10821436190402*sigma_th - 0.13956133*wtheta

In [58]:
eqs_hard_mm.iloc[7,4]

-1.09928536557669*sigma_th - 0.13448471*wtheta - (-dTheta_dz - 0.24348535)*(sigma_2 + 1.3679011)

In [ ]:
df_coefs = pd.DataFrame(columns = ['File', 'Avg Ustar', 'Avg Tau', 'Ug', 'Q', 'RMSE', 'R2', 'C1', 'C2', 'C3'])

for item in selected_files:
    #file
    # print(item)
    ds_stat = nc.Dataset(os.path.join(path, item), mode='r')

    #ustar
    ustar = ds_stat.groups['default'].variables['ustar'][:]
    # print("Mean of ustar: ", np.mean(ustar))

    #tau
    grr = 9.8
    T_0 = 300
    beta = grr/T_0
    pbl_height = ds_stat.groups['thermo'].variables['zi'][:]
    wtheta_surface = ds_stat.groups['thermo']['th_flux'][:,0]  
    wstar = np.power( beta * (wtheta_surface) * pbl_height , 1/3) 
    tau = pbl_height/wstar
    # print("Mean of tau: ", np.mean(tau))

    #ug and q
    ug, q = extract_ug_q(item)
    # print("Ug: ", ug)
    # print("Q: ", q)

    #rmse, r2
    fitted_model, X_train, X_test, y_train, y_test, rmse, r2, coefficients = LES_linear_regressor(path, [item], 
                                                                                                  time_avg = 15, 
                                                                                                  indices = np.s_[:, 0:200], 
                                                                                                  verbose = False)
    
    #c1, c2, c3
    c1 = coefficients[0]
    c2 = coefficients[1]
    c3 = coefficients[2]

    # Create a new row to be appended
    new_row = {
        'File': item,
        'Avg Ustar': np.mean(ustar),
        'Avg Tau': np.mean(tau),
        'Ug': ug,
        'Q': q,
        'RMSE': rmse,
        'R2': r2,
        'C1': c1,
        'C2': c2,
        'C3': c3
    }

    # Append the new row to the DataFrame
    df_coefs = pd.concat([df_coefs, pd.DataFrame([new_row])], ignore_index=True)

    # print("")

In [ ]:
df_coefs['Inversion Strength'] = [4, 4, 4, 4, 2, 4, 3, 2, 3, 4, 4]
df_coefs['C1'] = df_coefs['C1']* df_coefs['Avg Tau']
df_coefs['C2'] = df_coefs['C2']/beta
df_coefs['C1'] = np.abs(df_coefs['C1'])
df_coefs['C2'] = np.abs(df_coefs['C2'])
df_coefs['C3'] = np.abs(df_coefs['C3'])

In [ ]:
df_coefs

In [ ]:
# Define the variables and their respective labels and colors
variables = ['Q', 'Ug', 'Avg Tau', 'Avg Ustar', 'Inversion Strength']
xlabels = ['Q', 'Ug', 'Avg Tau', 'Avg Ustar', 'SI']
titles = [
    'C1 (wtheta) Values in Relation to {}', 
    'C2 (theta2) Values in Relation to {}', 
    'C3 (multiply) Values in Relation to {}'
]
colors = ['red', 'green', 'blue']
columns = ['C1', 'C2', 'C3']

# Loop through each variable to create scatter plots
for var, xlabel in zip(variables, xlabels):
    plt.figure(figsize=(12, 4))
    
    for i, (col, color, title) in enumerate(zip(columns, colors, titles)):
        plt.subplot(1, 3, i + 1)
        plt.scatter(df_coefs[var], df_coefs[col], label=col, marker='o', color=color)
        plt.xlabel(xlabel)
        plt.ylabel(f'{col} Values')
        plt.title(title.format(xlabel))
        plt.legend()
    
    plt.tight_layout()
    plt.show()

# Special case for box plots for 'Inversion Strength'
plt.figure(figsize=(12, 4))

for i, col in enumerate(columns):
    plt.subplot(1, 3, i + 1)
    df_coefs.boxplot(column=col, by='Inversion Strength', grid=False, ax=plt.gca(), patch_artist=True)
    plt.xlabel('SI')
    plt.ylabel(f'{col} Values')
    plt.title(f'{col} (wtheta) Values in Relation to SI')
    plt.suptitle('')  # Suppress the automatic title

plt.tight_layout()
plt.show()


In [ ]:
###### Is there any relationship between fit and the forcings??? ################
plt.figure(figsize=(16, 4))

# Plot R2 vs. Q
plt.subplot(1, 4, 1)
plt.scatter(df_coefs['Q'], df_coefs['R2'], label='R2', marker='o', color='red')
plt.xlabel('Q')
plt.ylabel('R2 Values')
plt.title('R2 Values in Relation to Q')
plt.legend()

# Plot R2 vs. Ug
plt.subplot(1, 4, 2)
plt.scatter(df_coefs['Ug'], df_coefs['R2'], label='R2', marker='o', color='green')
plt.xlabel('Ug')
plt.ylabel('R2 Values')
plt.title('R2 Values in Relation to Ug')
plt.legend()

# Plot R2 vs. Avg Tau
plt.subplot(1, 4, 3)
plt.scatter(df_coefs['Avg Tau'], df_coefs['R2'], label='R2', marker='o', color='blue')
plt.xlabel('Avg Tau')
plt.ylabel('R2 Values')
plt.title('R2 Values in Relation to Avg Tau')
plt.legend()

# Plot R2 vs. Avg Ustar
plt.subplot(1, 4, 4)
plt.scatter(df_coefs['Avg Ustar'], df_coefs['R2'], label='R2', marker='o', color='darkmagenta')
plt.xlabel('Avg Ustar')
plt.ylabel('R2 Values')
plt.title('R2 Values in Relation to Avg Ustar')
plt.legend()

# Adjust layout to prevent overlap
plt.tight_layout()

# Show the plot
plt.show()


In [ ]:
###### Is there any relationship between fit and the forcings??? ################
plt.figure(figsize=(16, 4))

# Plot RMSE vs. Q
plt.subplot(1, 4, 1)
plt.scatter(df_coefs['Q'], df_coefs['RMSE'], label='RMSE', marker='o', color='red')
plt.xlabel('Q')
plt.ylabel('RMSE Values')
plt.title('RMSE Values in Relation to Q')
plt.legend()

# Plot RMSE vs. Ug
plt.subplot(1, 4, 2)
plt.scatter(df_coefs['Ug'], df_coefs['RMSE'], label='RMSE', marker='o', color='green')
plt.xlabel('Ug')
plt.ylabel('RMSE Values')
plt.title('RMSE Values in Relation to Ug')
plt.legend()

# Plot RMSE vs. Avg Tau
plt.subplot(1, 4, 3)
plt.scatter(df_coefs['Avg Tau'], df_coefs['RMSE'], label='RMSE', marker='o', color='blue')
plt.xlabel('Avg Tau')
plt.ylabel('RMSE Values')
plt.title('RMSE Values in Relation to Avg Tau')
plt.legend()

# Plot RMSE vs. Avg Ustar
plt.subplot(1, 4, 4)
plt.scatter(df_coefs['Avg Ustar'], df_coefs['RMSE'], label='RMSE', marker='o', color='purple')
plt.xlabel('Avg Ustar')
plt.ylabel('RMSE Values')
plt.title('RMSE Values in Relation to Avg Ustar')
plt.legend()

# Adjust layout to prevent overlap
plt.tight_layout()

# Show the plot
plt.show()


In [ ]:
# Define the variable pairs and their respective labels
variable_pairs = [
    ('Ug', 'Q'), 
    ('Ug', 'Avg Tau'), 
    ('Ug', 'Avg Ustar'), 
    ('Q', 'Avg Tau'), 
    ('Q', 'Avg Ustar'), 
    ('Avg Tau', 'Avg Ustar')
]

xlabel_pairs = [
    ('Q', 'Ug'), 
    ('Avg Tau', 'Ug'), 
    ('Avg Ustar', 'Ug'), 
    ('Avg Tau', 'Q'), 
    ('Avg Ustar', 'Q'), 
    ('Avg Ustar', 'Avg Tau')
]

# Function to create heatmap
def create_heatmap(ax, x_grid, y_grid, C, xlabel, ylabel, title):
    heatmap = ax.pcolormesh(x_grid, y_grid, C, shading='auto', cmap='viridis')
    ax.set_xlabel(xlabel)
    ax.set_ylabel(ylabel)
    ax.set_title(title)
    plt.colorbar(heatmap, ax=ax)

# Loop through each variable pair to create the plots
for (var1, var2), (xlabel, ylabel) in zip(variable_pairs, xlabel_pairs):
    # Pivot tables to create 2D arrays
    C1_grid = df_coefs.pivot_table(index=var1, columns=var2, values='C1')
    C2_grid = df_coefs.pivot_table(index=var1, columns=var2, values='C2')
    C3_grid = df_coefs.pivot_table(index=var1, columns=var2, values='C3')

    # Create a meshgrid for var1 and var2
    x_values = C1_grid.columns
    y_values = C1_grid.index
    x_grid, y_grid = np.meshgrid(x_values, y_values)

    # Plot the heatmaps
    fig, axes = plt.subplots(1, 3, figsize=(18, 5))

    create_heatmap(axes[0], x_grid, y_grid, C1_grid.values, xlabel, ylabel, f'Heatmap of C1 ({xlabel} vs {ylabel})')
    create_heatmap(axes[1], x_grid, y_grid, C2_grid.values, xlabel, ylabel, f'Heatmap of C2 ({xlabel} vs {ylabel})')
    create_heatmap(axes[2], x_grid, y_grid, C3_grid.values, xlabel, ylabel, f'Heatmap of C3 ({xlabel} vs {ylabel})')

    plt.tight_layout()
    plt.show()



In [ ]:
# Scatter plot of C2 and C3
plt.figure(figsize=(7, 4))
plt.scatter(df_coefs['C2'], df_coefs['C3'], marker='o', color='darkcyan', label='C2 vs C3')

# Adding labels and title
plt.xlabel('C2 Values')
plt.ylabel('C3 Values')
plt.title('Scatter Plot of C2 vs C3')
plt.legend()

# Show the plot
plt.show()


In [ ]:
df_coefs

In [ ]:
df_X_l = df_coefs[['Avg Ustar', 'Avg Tau', 'Ug', 'Q']]

#normalize the columns of df_X_l using the min max normalization
df_X_l = (df_X_l - df_X_l.min()) / (df_X_l.max() - df_X_l.min())

df_X_l = df_X_l.rename(columns={'Avg Ustar': 'Ustar', 'Avg Tau': 'Tau', 'Q': 'Q_ic'})
df_C1 = df_coefs['C1']
df_C2 = df_coefs['C2']
df_C3 = df_coefs['C3']

In [ ]:
df_X_l

In [ ]:
df_c1_eqs = discover_coef_eqs(df_X_l, df_C1)

In [ ]:
df_c1_eqs

In [ ]:
df_c2_eqs = discover_coef_eqs(df_X_l, df_C2)

In [ ]:
df_c2_eqs

In [ ]:
df_c3_eqs = discover_coef_eqs(df_X_l, df_C3)

In [ ]:
df_c3_eqs

- normalize the data, then do symbolic regression. see how well that works. 
- try both min max and z score normalization

- (maybe create jittered/noisy variables for better fit, look up how much paper needs)

other things to think abt: 
- ustar in front of third term (punished coefficient complexity) (think abt)
- parametrization for dwwtheta/dz

final presi will be: 
1. the problem (background on turbulence, atmospheric boundary layer, etc)
2. the methodology (PYSR, how does it work, genetic algorithms, etc)
3. Re-disovery of the original equation.
4. Current work on improving the parametrization.

Sara will decide how she wants us to present: Hopefully either all three, or Laura and Greta together and then me separate. 